In [1]:
## import all required libraries
import pandas as pd # for data manipulation 
import numpy as np # for numerical calculation
import matplotlib.pyplot as plt # for data visualization
import seaborn as sns # for advance data visualization

from pulp import* # for solve the linear programing  problem
from sqlalchemy import create_engine # to connect the sql database 

In [2]:
# Set the maximum number of columns to be displayed
pd.set_option('display.max_columns', None)

In [3]:
# Load the data 
sand = pd.read_excel(r'C:\Users\Dell\Desktop\DS Project\Robo Sand(New Data).xlsx')

In [4]:
sand.rename(columns = {'Customer/Vendor Name':"Party Name",'Distribution Rule':"Warehouse",'U Km':"Distance","Quantity":"Net Weight"},inplace = True)

In [5]:
# check the null values and their sum
sand.isna().sum()
sand = sand.dropna() # drop null values

In [6]:
# unique warehouses and party_names
warehouses = sand['Warehouse'].unique()
party_names = sand['Party Name'].unique()

In [7]:
# shows Unique Warehouses and Party Names
print(warehouses)
print("\n")
print(party_names)

['GIRMAPUR' 'GIRMAPR2' 'KEESARA3' 'LKDRM2' 'LKDRM4' 'RSDSH' 'SLKPY']


['URBANRISE LIFESTYLES PRIVATE LIMITED - IDA BOLLARAM'
 'MUPPA PROJECTS INDIA PVT LTD - OSMAN NAGAR'
 'SHAPOORJI PALLONJI AND COMPANY PRIVATE LIMITED - KANDI' ...
 'SATYAVARDHAN REDDY VALLAM REDDY - KONDAPUR'
 'SRIJA CONSTRUCTIONS - NALLAGANDLA'
 'VISHEESHTA INFRACON LLP - MOUTHNAGAR']


In [8]:
sand['Freight_Rate'] = 0
for i in sand.index:
    if (sand['Warehouse'][i] == 'GIRMAPUR'):
        sand.at[i, 'Freight_Rate'] = 2.5
    elif (sand['Warehouse'][i] == 'GIRMAPR2'):
        sand.at[i, 'Freight_Rate'] = 2.5    
    elif (sand['Warehouse'][i] == 'KEESARA3'):
        sand.at[i, 'Freight_Rate'] = 2.5
    elif (sand['Warehouse'][i] == 'LKDRM2'):
        sand.at[i, 'Freight_Rate'] = 2.5
    elif (sand['Warehouse'][i] == 'LKDRM4'):
        sand.at[i, 'Freight_Rate'] = 2.5
    elif (sand['Warehouse'][i] == 'RSDSH') :
        sand.at[i, 'Freight_Rate'] = 2.5
    elif (sand['Warehouse'][i] == 'SLKPY') :
        sand.at[i, 'Freight_Rate'] = 2.5

In [9]:
sand["Total Cost"] = 0
for i in sand.index:
    sand.at[i, "Total Cost"] = sand.at[i, 'Freight_Rate'] * sand.at[i, 'Distance'] * sand.at[i, 'Net Weight']

In [10]:
# Create the cost matric with respective to Warehouse and party cosider minimum cost per KM per MT in ₹
cost_mat = sand.pivot_table(values = 'Freight_Rate', index = 'Warehouse', columns = 'Party Name', aggfunc = 'min')

In [11]:
# fill with high value (100000) wherever not supplied the sand  
cost_mat.fillna(100000, inplace = True)
cost_mat.head()

Party Name  1000 PILLAR S CONSTRUCTIONS - HAFEEZPET.  \
Warehouse                                              
GIRMAPR2                                         2.5   
GIRMAPUR                                         2.5   
KEESARA3                                    100000.0   
LKDRM2                                      100000.0   
LKDRM4                                      100000.0   

Party Name  1000 PILLARS ORCHID DEVELOPERS  \
Warehouse                                    
GIRMAPR2                          100000.0   
GIRMAPUR                          100000.0   
KEESARA3                               2.5   
LKDRM2                            100000.0   
LKDRM4                            100000.0   

Party Name  2D PHARMACEUTICALS PRIVATE LIMITED -  MALLAPUR  \
Warehouse                                                    
GIRMAPR2                                          100000.0   
GIRMAPUR                                          100000.0   
KEESARA3                                               2.5   
LKDRM2                                            100000.0   
LKDRM4                                            100000.0   

Party Name  2D PHARMACEUTICALS PRIVATE LIMITED - BANDLAGUDA  \
Warehouse                                                     
GIRMAPR2                                           100000.0   
GIRMAPUR                                           100000.0   
KEESARA3                                                2.5   
LKDRM2                                             100000.0   
LKDRM4                                             100000.0   

Party Name  7 HILLS CONCRETE SOLUTIONS PVT LTD - GANDIMISAMMA  \
Warehouse                                                       
GIRMAPR2                                                  2.5   
GIRMAPUR                                                  2.5   
KEESARA3                                             100000.0   
LKDRM2                                               100000.0   
LKDRM4                                               100000.0   

Party Name  7HILLS INFRA CONCRETE - GANDIMAISAMMA  \
Warehouse                                           
GIRMAPR2                                      2.5   
GIRMAPUR                                      2.5   
KEESARA3                                 100000.0   
LKDRM2                                   100000.0   
LKDRM4                                   100000.0   

Party Name  A & S BUILDR HOMETECH LLP - DAMMAIGUDA  A ANITHA - RAMPALLY  \
Warehouse                                                                 
GIRMAPR2                                  100000.0             100000.0   
GIRMAPUR                                  100000.0             100000.0   
KEESARA3                                  100000.0                  2.5   
LKDRM2                                    100000.0             100000.0   
LKDRM4                                    100000.0             100000.0   

Party Name  A H CONSTRUCTIONS - CHOWDARIGUDA  A KOMALA - BOWRAMPET  \
Warehouse                                                            
GIRMAPR2                            100000.0                   2.5   
GIRMAPUR                            100000.0                   2.5   
KEESARA3                                 2.5              100000.0   
LKDRM2                              100000.0              100000.0   
LKDRM4                              100000.0              100000.0   

Party Name  A KOMALA - BUCHUPALLY  A R ANMOL DEVELOPERS - PATANCHERUVU  \
Warehouse                                                                
GIRMAPR2                      2.5                                  2.5   
GIRMAPUR                      2.5                                  2.5   
KEESARA3                 100000.0                             100000.0   
LKDRM2                        2.5                                  2.5   
LKDRM4                   100000.0                                  2.5   

Party Name  A R BULDERS - UPPAL  A R CONSTR

In [12]:
# Create a pivot table with Warehouse as index, Party Name as columns, and Distance as values
distance_matrix = sand.pivot_table(values='Distance', index='Warehouse', columns='Party Name')
# fill with 1000 Wherever no supply
distance_matrix.fillna(1000, inplace = True)
distance_matrix.head()

Party Name  1000 PILLAR S CONSTRUCTIONS - HAFEEZPET.  \
Warehouse                                              
GIRMAPR2                                      68.456   
GIRMAPUR                                      68.178   
KEESARA3                                    1000.000   
LKDRM2                                      1000.000   
LKDRM4                                      1000.000   

Party Name  1000 PILLARS ORCHID DEVELOPERS  \
Warehouse                                    
GIRMAPR2                            1000.0   
GIRMAPUR                            1000.0   
KEESARA3                              62.5   
LKDRM2                              1000.0   
LKDRM4                              1000.0   

Party Name  2D PHARMACEUTICALS PRIVATE LIMITED -  MALLAPUR  \
Warehouse                                                    
GIRMAPR2                                          1000.000   
GIRMAPUR                                          1000.000   
KEESARA3                                            68.066   
LKDRM2                                            1000.000   
LKDRM4                                            1000.000   

Party Name  2D PHARMACEUTICALS PRIVATE LIMITED - BANDLAGUDA  \
Warehouse                                                     
GIRMAPR2                                           1000.000   
GIRMAPUR                                           1000.000   
KEESARA3                                             87.572   
LKDRM2                                             1000.000   
LKDRM4                                             1000.000   

Party Name  7 HILLS CONCRETE SOLUTIONS PVT LTD - GANDIMISAMMA  \
Warehouse                                                       
GIRMAPR2                                               29.944   
GIRMAPUR                                               29.668   
KEESARA3                                             1000.000   
LKDRM2                                               1000.000   
LKDRM4                                               1000.000   

Party Name  7HILLS INFRA CONCRETE - GANDIMAISAMMA  \
Warehouse                                           
GIRMAPR2                                   30.050   
GIRMAPUR                                   29.774   
KEESARA3                                 1000.000   
LKDRM2                                   1000.000   
LKDRM4                                   1000.000   

Party Name  A & S BUILDR HOMETECH LLP - DAMMAIGUDA  A ANITHA - RAMPALLY  \
Warehouse                                                                 
GIRMAPR2                                    1000.0             1000.000   
GIRMAPUR                                    1000.0             1000.000   
KEESARA3                                    1000.0               51.056   
LKDRM2                                      1000.0             1000.000   
LKDRM4                                      1000.0             1000.000   

Party Name  A H CONSTRUCTIONS - CHOWDARIGUDA  A KOMALA - BOWRAMPET  \
Warehouse                                                            
GIRMAPR2                            1000.000                43.264   
GIRMAPUR                            1000.000                42.998   
KEESARA3                              64.516              1000.000   
LKDRM2                              1000.000              1000.000   
LKDRM4                              1000.000              1000.000   

Party Name  A KOMALA - BUCHUPALLY  A R ANMOL DEVELOPERS - PATANCHERUVU  \
Warehouse                                                                
GIRMAPR2                   49.542                               63.746   
GIRMAPUR                   49.266                               62.588   
KEESARA3                 1000.000                             1000.000   
LKDRM2                     56.632                               30.980   
LKDRM4                   1000.000                               29.932   

Party Name  A R BULDERS - UPPAL  A R CONSTR

In [13]:
# create pivot_table for quantity of sand transporte index as Warehouse and columns Party values are Net_weight
weight_mat = sand.pivot_table(values = 'Net Weight', index = 'Warehouse', columns = 'Party Name', aggfunc =sum )
# fill with zeros wherever no sulpply 
weight_mat = weight_mat.fillna(0)
weight_mat.head()

Party Name  1000 PILLAR S CONSTRUCTIONS - HAFEEZPET.  \
Warehouse                                              
GIRMAPR2                                      324.36   
GIRMAPUR                                      171.00   
KEESARA3                                        0.00   
LKDRM2                                          0.00   
LKDRM4                                          0.00   

Party Name  1000 PILLARS ORCHID DEVELOPERS  \
Warehouse                                    
GIRMAPR2                              0.00   
GIRMAPUR                              0.00   
KEESARA3                             18.82   
LKDRM2                                0.00   
LKDRM4                                0.00   

Party Name  2D PHARMACEUTICALS PRIVATE LIMITED -  MALLAPUR  \
Warehouse                                                    
GIRMAPR2                                              0.00   
GIRMAPUR                                              0.00   
KEESARA3                                            203.58   
LKDRM2                                                0.00   
LKDRM4                                                0.00   

Party Name  2D PHARMACEUTICALS PRIVATE LIMITED - BANDLAGUDA  \
Warehouse                                                     
GIRMAPR2                                               0.00   
GIRMAPUR                                               0.00   
KEESARA3                                              77.16   
LKDRM2                                                 0.00   
LKDRM4                                                 0.00   

Party Name  7 HILLS CONCRETE SOLUTIONS PVT LTD - GANDIMISAMMA  \
Warehouse                                                       
GIRMAPR2                                               531.56   
GIRMAPUR                                               797.70   
KEESARA3                                                 0.00   
LKDRM2                                                   0.00   
LKDRM4                                                   0.00   

Party Name  7HILLS INFRA CONCRETE - GANDIMAISAMMA  \
Warehouse                                           
GIRMAPR2                                   217.37   
GIRMAPUR                                   113.94   
KEESARA3                                     0.00   
LKDRM2                                       0.00   
LKDRM4                                       0.00   

Party Name  A & S BUILDR HOMETECH LLP - DAMMAIGUDA  A ANITHA - RAMPALLY  \
Warehouse                                                                 
GIRMAPR2                                       0.0                 0.00   
GIRMAPUR                                       0.0                 0.00   
KEESARA3                                       0.0               131.09   
LKDRM2                                         0.0                 0.00   
LKDRM4                                         0.0                 0.00   

Party Name  A H CONSTRUCTIONS - CHOWDARIGUDA  A KOMALA - BOWRAMPET  \
Warehouse                                                            
GIRMAPR2                                 0.0                102.31   
GIRMAPUR                                 0.0                401.03   
KEESARA3                               253.4                  0.00   
LKDRM2                                   0.0                  0.00   
LKDRM4                                   0.0                  0.00   

Party Name  A KOMALA - BUCHUPALLY  A R ANMOL DEVELOPERS - PATANCHERUVU  \
Warehouse                                                                
GIRMAPR2                   396.59                               151.74   
GIRMAPUR                   841.19                                22.56   
KEESARA3                     0.00                                 0.00   
LKDRM2                      27.60                              1498.94   
LKDRM4                       0.00                                94.78   

Party Name  A R BULDERS - UPPAL  A R CONSTR

In [14]:
# create pivot table with warehouse as index and net weight sum
supply = pd.pivot_table(sand, values='Net Weight', index=['Warehouse'], aggfunc=sum, margins=True)
supply

Net Weight
Warehouse             
GIRMAPR2    436823.344
GIRMAPUR    500290.587
KEESARA3    275107.765
LKDRM2      347263.755
LKDRM4       21874.161
RSDSH        64687.640
SLKPY       140448.760
All        1786496.012

In [15]:
#create a pivot_tabel for total demand of each party (Before optimization the Quantity of sand Transport from Warehouse the Party)
demand = pd.pivot_table(sand, values='Net Weight', index ='Warehouse', columns ='Party Name', aggfunc = sum, margins =True, margins_name='Grand Total')
demand

Party Name   1000 PILLAR S CONSTRUCTIONS - HAFEEZPET.  \
Warehouse                                               
GIRMAPR2                                       324.36   
GIRMAPUR                                       171.00   
KEESARA3                                          NaN   
LKDRM2                                            NaN   
LKDRM4                                            NaN   
RSDSH                                             NaN   
SLKPY                                             NaN   
Grand Total                                    495.36   

Party Name   1000 PILLARS ORCHID DEVELOPERS  \
Warehouse                                     
GIRMAPR2                                NaN   
GIRMAPUR                                NaN   
KEESARA3                              18.82   
LKDRM2                                  NaN   
LKDRM4                                  NaN   
RSDSH                                   NaN   
SLKPY                                   NaN   
Grand Total                           18.82   

Party Name   2D PHARMACEUTICALS PRIVATE LIMITED -  MALLAPUR  \
Warehouse                                                     
GIRMAPR2                                                NaN   
GIRMAPUR                                                NaN   
KEESARA3                                             203.58   
LKDRM2                                                  NaN   
LKDRM4                                                  NaN   
RSDSH                                                 57.70   
SLKPY                                                   NaN   
Grand Total                                          261.28   

Party Name   2D PHARMACEUTICALS PRIVATE LIMITED - BANDLAGUDA  \
Warehouse                                                      
GIRMAPR2                                                 NaN   
GIRMAPUR                                                 NaN   
KEESARA3                                               77.16   
LKDRM2                                                   NaN   
LKDRM4                                                   NaN   
RSDSH                                                    NaN   
SLKPY                                                    NaN   
Grand Total                                            77.16   

Party Name   7 HILLS CONCRETE SOLUTIONS PVT LTD - GANDIMISAMMA  \
Warehouse                                                        
GIRMAPR2                                                531.56   
GIRMAPUR                                                797.70   
KEESARA3                                                   NaN   
LKDRM2                                                     NaN   
LKDRM4                                                     NaN   
RSDSH                                                      NaN   
SLKPY                                                      NaN   
Grand Total                                            1329.26   

Party Name   7HILLS INFRA CONCRETE - GANDIMAISAMMA  \
Warehouse                                            
GIRMAPR2                                    217.37   
GIRMAPUR                                    113.94   
KEESARA3                                       NaN   
LKDRM2                                         NaN   
LKDRM4                                         NaN   
RSDSH                                          NaN   
SLKPY                                          NaN   
Grand Total                                 331.31   

Party Name   A & S BUILDR HOMETECH LLP - DAMMAIGUDA  A ANITHA - RAMPALLY  \
Warehouse                                                                  
GIRMAPR2                                        NaN                  NaN   
GIRMAPUR                                        NaN                  NaN   
KEESARA3                                        NaN               131.09   
LKDRM2                                          NaN                  NaN   
LKDRM4                      

In [16]:
# Only consider the Demand 
demand = demand.iloc[7:]
# Rename the column
demand.rename(index= {'Grand Total': 'Demand'}, inplace = True)
demand.head()

C:\Users\Dell\AppData\Local\Temp\ipykernel_5812\1764422176.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  demand.rename(index= {'Grand Total': 'Demand'}, inplace = True)


Party Name  1000 PILLAR S CONSTRUCTIONS - HAFEEZPET.  \
Warehouse                                              
Demand                                        495.36   

Party Name  1000 PILLARS ORCHID DEVELOPERS  \
Warehouse                                    
Demand                               18.82   

Party Name  2D PHARMACEUTICALS PRIVATE LIMITED -  MALLAPUR  \
Warehouse                                                    
Demand                                              261.28   

Party Name  2D PHARMACEUTICALS PRIVATE LIMITED - BANDLAGUDA  \
Warehouse                                                     
Demand                                                77.16   

Party Name  7 HILLS CONCRETE SOLUTIONS PVT LTD - GANDIMISAMMA  \
Warehouse                                                       
Demand                                                1329.26   

Party Name  7HILLS INFRA CONCRETE - GANDIMAISAMMA  \
Warehouse                                           
Demand                                     331.31   

Party Name  A & S BUILDR HOMETECH LLP - DAMMAIGUDA  A ANITHA - RAMPALLY  \
Warehouse                                                                 
Demand                                       65.38               131.09   

Party Name  A H CONSTRUCTIONS - CHOWDARIGUDA  A KOMALA - BOWRAMPET  \
Warehouse                                                            
Demand                                 253.4                503.34   

Party Name  A KOMALA - BUCHUPALLY  A R ANMOL DEVELOPERS - PATANCHERUVU  \
Warehouse                                                                
Demand                    1265.38                              1768.02   

Party Name  A R BULDERS - UPPAL  A R CONSTRUCTIONS - MACHABOLLARAM  \
Warehouse                                                            
Demand                   802.54                             225.95   

Party Name  A R K  BUILDERS - ADIBATLA  \
Warehouse                                
Demand                          167.69   

Party Name  A R R CONSTRUCTIONS & DEVELOPERS - GACHIBOWLI  \
Warehouse                                                   
Demand                                             108.14   

Party Name  A RAJI REDDY - UPPAL HMDA LAYOUT  A RAMESH REDDY - YAPRAL  \
Warehouse                                                               
Demand                                 78.41                    76.92   

Party Name  A S CONSTRUCTIONS - KPHB  A S CONSTRUCTIONS - KUKATPALLY  \
Warehouse                                                              
Demand                        132.01                           48.57   

Party Name  A S CONSTRUCTIONS - PRAGATHI NAGAR  A SANTOSH TEJA - RAMPALLI  \
Warehouse                                                                   
Demand                                  443.12                       25.2   

Party Name  A U CONSTRUCTIONS - GACHIBOWLI  A V L CONSTRUCTIONS - PUPPALAGUDA  \
Warehouse                                                                       
Demand                              252.33                            1485.85   

Party Name  A VENKATESH - ALMASGUDA  A.J.S. CONSTRUCTIONS - PEERZADIGUDA  \
Warehouse                                                                  
Demand                       251.02                                94.86   

Party Name  A.J.S. CONSTRUCTIONS - RAMACHANDRAPURAM  \
Warehouse                                             
Demand                                       794.51   

Party Name  A.SIDDA REDDY - BRAHMANAPALLY  AACESS EQUIPMENTS - KUKATPALLY  \
Warehouse                                                                   
Demand                              48.84                           476.1   

Party Name  AAKANKSHA ORION HOMES - SHANKARPALLY  \
Warehouse                                          
Demand                                   2258.77   

Party Name  AAKRITI CONSTRUCTIONS AND DEVELOPERS PVT LTD  \
Warehouse           

In [17]:
# Define the problem
prob = LpProblem("Transportation Problem", LpMinimize)

C:\Users\Dell\.anaconda\anaconda\lib\site-packages\pulp\pulp.py:1352: UserWarning: Spaces are not permitted in the name. Converted to '_'
  warnings.warn("Spaces are not permitted in the name. Converted to '_'")


In [18]:
# Define decision variables
route_vars = LpVariable.dicts("Route", (warehouses, party_names), lowBound=0, cat='Continuous')
route_vars

{'GIRMAPUR': {'URBANRISE LIFESTYLES PRIVATE LIMITED - IDA BOLLARAM': Route_GIRMAPUR_URBANRISE_LIFESTYLES_PRIVATE_LIMITED___IDA_BOLLARAM,
  'MUPPA PROJECTS INDIA PVT LTD - OSMAN NAGAR': Route_GIRMAPUR_MUPPA_PROJECTS_INDIA_PVT_LTD___OSMAN_NAGAR,
  'SHAPOORJI PALLONJI AND COMPANY PRIVATE LIMITED - KANDI': Route_GIRMAPUR_SHAPOORJI_PALLONJI_AND_COMPANY_PRIVATE_LIMITED___KANDI,
  'SILVER LINE CONSTRUCTIONS - POTHARAM': Route_GIRMAPUR_SILVER_LINE_CONSTRUCTIONS___POTHARAM,
  'GREATER INFRA PROJECTS PRIVATE LIMITED - BACHUPALLY': Route_GIRMAPUR_GREATER_INFRA_PROJECTS_PRIVATE_LIMITED___BACHUPALLY,
  'SHARADHA DEVELOPERS -  NARIGUDA': Route_GIRMAPUR_SHARADHA_DEVELOPERS____NARIGUDA,
  'SVS INFRACON PRIVATE LIMITED - CHANDANAGAR': Route_GIRMAPUR_SVS_INFRACON_PRIVATE_LIMITED___CHANDANAGAR,
  'VR ELITE BUILDERS AND DEVELOPERS - AMEENPUR': Route_GIRMAPUR_VR_ELITE_BUILDERS_AND_DEVELOPERS___AMEENPUR,
  'M S HOMES - BOWRAMPET': Route_GIRMAPUR_M_S_HOMES___BOWRAMPET,
  'URBAN UNNATI HOMES - BAHUDURPALLY': 

In [19]:
# Define the objective function
prob += lpSum([route_vars[w][p] * cost_mat.loc[w][p] * distance_matrix.loc[w][p] for w in warehouses for p in party_names]), " Transportation Cost"

In [20]:
# Define the constraints supply(Actual supplied == Warehouse_Capacity )
for w in warehouses:
    prob += lpSum([route_vars[w][p]   for p in party_names]) <= supply.loc[w] , "Sum of quatity supplied from Warehouse to paty %s" % w

In [21]:
demand2 = demand.T
print(demand2.head(10))

Warehouse                                           Demand
Party Name                                                
1000 PILLAR S CONSTRUCTIONS - HAFEEZPET.            495.36
1000 PILLARS ORCHID DEVELOPERS                       18.82
2D PHARMACEUTICALS PRIVATE LIMITED -  MALLAPUR      261.28
2D PHARMACEUTICALS PRIVATE LIMITED - BANDLAGUDA      77.16
7 HILLS CONCRETE SOLUTIONS PVT LTD - GANDIMISAMMA  1329.26
7HILLS INFRA CONCRETE - GANDIMAISAMMA               331.31
A & S BUILDR HOMETECH LLP - DAMMAIGUDA               65.38
A ANITHA - RAMPALLY                                 131.09
A H CONSTRUCTIONS - CHOWDARIGUDA                    253.40
A KOMALA - BOWRAMPET                                503.34


In [22]:
# demand constraints(The Quantity of sand Recivied = Actual Demand)
for p in party_names:
    prob+= lpSum([route_vars[w][p] for w in warehouses]) >= demand2.loc[p],'sum of Demand of the party %s'%p

In [23]:
# Execute the problem
prob.solve()
print('Total_transportation_Costs = {:,} '.format(int(value(prob.objective))))

Total_transportation_Costs = 264,924,781 


In [24]:
# shows the status of the Problem
print(f"Status: {LpStatus[prob.status]}")

Status: Optimal


In [25]:
# Create DataFrame 
decision_var_df = pd.DataFrame(index=distance_matrix.index, columns=distance_matrix.columns, dtype='float')

In [26]:
# Fill the DataFrame with the optimized values of the decision variables
for w in distance_matrix.index:
    for p in distance_matrix.columns:
        decision_var_df.loc[w, p] = route_vars[w][p].varValue

In [27]:
# Decision_Variables(How Much Quantity of Sand Transport form Warehouse to Party )
decision_var_df.head()

Party Name  1000 PILLAR S CONSTRUCTIONS - HAFEEZPET.  \
Warehouse                                              
GIRMAPR2                                        0.00   
GIRMAPUR                                      495.36   
KEESARA3                                        0.00   
LKDRM2                                          0.00   
LKDRM4                                          0.00   

Party Name  1000 PILLARS ORCHID DEVELOPERS  \
Warehouse                                    
GIRMAPR2                              0.00   
GIRMAPUR                              0.00   
KEESARA3                             18.82   
LKDRM2                                0.00   
LKDRM4                                0.00   

Party Name  2D PHARMACEUTICALS PRIVATE LIMITED -  MALLAPUR  \
Warehouse                                                    
GIRMAPR2                                              0.00   
GIRMAPUR                                              0.00   
KEESARA3                                            261.28   
LKDRM2                                                0.00   
LKDRM4                                                0.00   

Party Name  2D PHARMACEUTICALS PRIVATE LIMITED - BANDLAGUDA  \
Warehouse                                                     
GIRMAPR2                                               0.00   
GIRMAPUR                                               0.00   
KEESARA3                                              77.16   
LKDRM2                                                 0.00   
LKDRM4                                                 0.00   

Party Name  7 HILLS CONCRETE SOLUTIONS PVT LTD - GANDIMISAMMA  \
Warehouse                                                       
GIRMAPR2                                                 0.00   
GIRMAPUR                                              1329.26   
KEESARA3                                                 0.00   
LKDRM2                                                   0.00   
LKDRM4                                                   0.00   

Party Name  7HILLS INFRA CONCRETE - GANDIMAISAMMA  \
Warehouse                                           
GIRMAPR2                                     0.00   
GIRMAPUR                                   331.31   
KEESARA3                                     0.00   
LKDRM2                                       0.00   
LKDRM4                                       0.00   

Party Name  A & S BUILDR HOMETECH LLP - DAMMAIGUDA  A ANITHA - RAMPALLY  \
Warehouse                                                                 
GIRMAPR2                                       0.0                 0.00   
GIRMAPUR                                       0.0                 0.00   
KEESARA3                                       0.0               131.09   
LKDRM2                                         0.0                 0.00   
LKDRM4                                         0.0                 0.00   

Party Name  A H CONSTRUCTIONS - CHOWDARIGUDA  A KOMALA - BOWRAMPET  \
Warehouse                                                            
GIRMAPR2                                 0.0                503.34   
GIRMAPUR                                 0.0                  0.00   
KEESARA3                               253.4                  0.00   
LKDRM2                                   0.0                  0.00   
LKDRM4                                   0.0                  0.00   

Party Name  A KOMALA - BUCHUPALLY  A R ANMOL DEVELOPERS - PATANCHERUVU  \
Warehouse                                                                
GIRMAPR2                  1265.38                                 0.00   
GIRMAPUR                     0.00                                 0.00   
KEESARA3                     0.00                                 0.00   
LKDRM2                       0.00                              1768.02   
LKDRM4                       0.00                                 0.00   

Party Name  A R BULDERS - UPPAL  A R CONSTR

In [28]:
# Verify the cost after Optimization
total_after_opt = [decision_var_df.loc[w][p] * cost_mat.loc[w][p] * distance_matrix.loc[w][p] .sum().sum() for w in warehouses for p in party_names]

In [29]:
total1 = sum(total_after_opt)
print('total_cost_after_opt',total1)

total_cost_after_opt 264924781.08953387


In [30]:
# Before_Optimization the Transportation Cost in ₹
before_opt_cost = sand['Amount'].sum()
before_opt_cost

309961448.44037455

In [31]:
#Total Cost - Total Minimized Cost 
print("Difference_ before- after:",(before_opt_cost) -  sum(total_after_opt))

Difference_ before- after: 45036667.35084069


In [32]:
# Calculating the percentage 
print("percentage_decrease:",((((before_opt_cost) -  sum(total_after_opt)))/((before_opt_cost)))*100)

percentage_decrease: 14.529764129523393


In [36]:
# save the cost_matric in csv formate
cost_mat.to_csv('cost_mat_final_1.csv')

In [37]:
# save the distance_matric in csv formate
distance_matrix.to_csv('distance_final_1.csv')

In [38]:
# save the decision_variable_matric in csv formate
decision_var_df.to_csv('final_decision_values1_1.csv')